In [1]:
import random

In [2]:
gameMap = ['go', 'cheap1', 'community', 'cheap3', 'parking', 'railroad','cheap6','chance','cheap8','medium9','jail',
       'medium11','utility','medium13','medium14','railroad','medium16','community','medium18','medium19','parking',
       'medium21','chance','medium23','medium24','railroad','medium26','medium27','utility','medium29','go to jail',
       'expensive31','expensive32','community','expensive34','railroad','chance','expensive37','parking','expensive39']

In [3]:
gameDict = {'go': [0], 'community': [2], 'parking': [0], 'railroad': [0], 'chance': [3], 'jail' : [0], 'go to jail':[4], 'utility' : [0],
           'cheap1':[1, 60, 10],'cheap3':[1, 60, 20],'cheap6':[1, 100,30],'cheap8':[1, 100, 30],
            'medium9':[1, 120, 40],'medium11':[1, 140, 50],'medium13':[1, 140, 50],'medium14':[1, 160, 60],'medium16':[1, 180, 70],
            'medium18':[1, 180, 70],'medium19':[1, 200, 80],'medium21':[1, 220, 90],'medium23':[1, 220, 90],'medium24':[1, 240, 100],
            'medium26':[1, 260, 110],'medium27':[1, 260, 110],'medium29':[1, 280, 120],
            'expensive31':[1, 300, 130],'expensive32':[1, 300, 130],'expensive34':[1, 320, 150],'expensive37':[1, 350, 175],'expensive39':[1, 400, 200]}

In [4]:
railRoad = [5, 15, 25 ,35]
debugSw = True

In [5]:
#id, position, debit, player type
player1 = [1, 0, 500, 1]
player2 = [2, 0, 500, 2]
playerList = [[0, 0 ,99999], player1, player2] #第一个是无效用户，ignore
housePurchase = [0] * 40

In [6]:
def diceOnce():
    return int(6 * random.random() + 1)

def debugPrint(Text1, Text2):
    if(debugSw):
        print(Text1, Text2)

In [7]:
def noBuy(value, player):
    return False

def buyCheap(value, player):
    if(value <= 100):
        return True
    return False

def buyMedium(value, player):
    if (value <= 280 and value > 100):
        return True
    return False

def buyExpensive(value, player):
    if (value > 280):
        return True
    return False

def buyCheapAndExpensive(value, player):
    if (value <= 100 or value > 280):
        return True
    return False

def buyCheapAndMedium(value, player):
    if (value <= 100  or (value <= 280 and value > 100)):
        return True
    return False

def buyExpensiveAndMedium(value, player):
    if (value > 280 or (value <= 280 and value > 100)):
        return True
    return False

def buyAll(value, player):
    return True

def buyWithSafeBudget(value, player):
    if player[2] >= 100:
        return True
    return False

In [8]:
strategy = [noBuy, buyCheap, buyMedium, buyExpensive,buyCheapAndExpensive,buyCheapAndMedium,buyExpensiveAndMedium,buyAll,buyWithSafeBudget]

In [9]:
def purchase(player):
    debugPrint("------------", "--")
    debugPrint("beforePurchase:", player)
    pos = player[1]
    value = gameDict[gameMap[pos]]
    posType = value[0]
    if posType != 1:
        return
    if(player[2] <= value[1]):
        return
    if(not strategy[player[3]](value[1],player)):
        return
    player[2] = player[2] - value[1]
    housePurchase[pos] = player[0]
    debugPrint("AfterPurchase:", player)

In [10]:
def needRent(player):
    pos = player[1]
    return housePurchase[pos] != 0 and housePurchase[pos] != player[0]

In [11]:
def rent(player):
    debugPrint("------------", "--")
    debugPrint("beforeRent:", player)
    pos = player[1]
    toPlayerId = housePurchase[pos]
    toPlayer = playerList[toPlayerId]
    rentValue = min(gameDict[gameMap[pos]][2], player[2])
    toPlayer[2] += rentValue;
    player[2] -=rentValue;
    debugPrint("Rent:", rentValue)
    debugPrint("AfterRent:", player)


In [12]:
def chance(player):
    debugPrint("------------", "--")
    chance_destiny_pos = [0, 5, 10, 11, 24, 39]
    utility = [12, 28]
    randValue = int(16 * random.random() + 1)
    debugPrint("beforeChance",player)
    debugPrint('randValue', randValue)
    pos = player[1]
    if(randValue <= 2):
        nearestRailPos = 0
        nearestValue = 9999
        for i in range(len(railRoad)):
            dist = railRoad[i]-pos
            if dist < 0:
                dist += 40
            if(dist<nearestValue):
                nearestRailPos = railRoad[i]
                nearestValue = dist
        player[1] = nearestRailPos
        debugPrint("afterChance",player)
        return
    if(randValue <= 3):
        player[1] -= 3
        debugPrint("afterChance",player)
        return
    if(randValue <= 4):
        nearestUtilityPos = 0
        nearestValue = 9999
        for i in range(len(utility)):
            dist = utility[i]-pos
            if dist < 0:
                dist += 40
            if(dist<nearestValue):
                nearestUtilityPos = utility[i]
                nearestValue = dist
        player[1] = nearestUtilityPos
        debugPrint("afterChance",player)
        return
    if(randValue <= 10):
        debugPrint("afterChance",player)
        return
    player[1]=chance_destiny_pos[randValue-11]
    debugPrint("afterChance",player)

In [13]:
def community(player):
    debugPrint("------------", "--")
    debugPrint("beforeCommunity",player)
    community_destiny_pos = [0, 10]
    randValue = int(16 * random.random() + 1)
    debugPrint("randValue",randValue)
    if (randValue <= 2):
        player[1]=community_destiny_pos[randValue-1]
    debugPrint("afterCommunity",player)

In [14]:
def game(MaxRound = 999999):
    curPlayerId = 1
    roundNumber = 0
    while(MaxRound > 0):
        MaxRound -= 1
        roundNumber += 1
        end = False
        for i in range(len(playerList)):
            if(playerList[i][2] <= 0):
                end = True
                print('result', playerList)
                return playerList[i][0];
        t1 = diceOnce()
        t2 = diceOnce()
        move = t1 + t2
        curPlayer = playerList[curPlayerId]
        posBeforeMove = curPlayer[1]
        curPos = posBeforeMove + move
        curPos = curPos % 40
        debugPrint("------------", "--")
        debugPrint('roundNumber', roundNumber)
        debugPrint('current PlayerId',curPlayerId)
        debugPrint('curent Position',curPos)
        debugPrint('curent Position Type',gameMap[curPos])
        posType = gameDict[gameMap[curPos]][0]
        if(posType == 0):
            playerList[curPlayerId][1] = curPos
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            continue
        if(posType == 4):
            playerList[curPlayerId][1] = 10
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            continue
        if(posType == 1):
            playerList[curPlayerId][1] = curPos
            if(housePurchase[curPos] == 0):
                purchase(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                continue
            if(needRent(playerList[curPlayerId])):
                rent(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                continue
        if(posType == 2):
            playerList[curPlayerId][1] = curPos
            community(playerList[curPlayerId])
            if(housePurchase[curPos] == 0):
                purchase(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                continue
            if(needRent(playerList[curPlayerId])):
                rent(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                continue
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            continue
        if(posType == 3):
            playerList[curPlayerId][1] = curPos
            chance(playerList[curPlayerId])
            if(housePurchase[curPos] == 0):
                purchase(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                continue
            if(needRent(playerList[curPlayerId])):
                rent(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                continue
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            continue

In [15]:
#id, position, debit, playerType
player1 = [1, 0, 500, 1]
player2 = [2, 0, 500, 2]
playerList = [[0, 0 ,99999], player1, player2]
housePurchase = [0] * 40
debugSw = True

In [16]:
game()

------------ --
roundNumber 1
current PlayerId 1
curent Position 5
curent Position Type railroad
------------ --
roundNumber 2
current PlayerId 2
curent Position 7
curent Position Type chance
------------ --
beforeChance [2, 7, 500, 2]
randValue 11
afterChance [2, 0, 500, 2]
------------ --
beforePurchase: [2, 0, 500, 2]
------------ --
roundNumber 3
current PlayerId 1
curent Position 9
curent Position Type medium9
------------ --
beforePurchase: [1, 9, 500, 1]
------------ --
roundNumber 4
current PlayerId 2
curent Position 4
curent Position Type parking
------------ --
roundNumber 5
current PlayerId 1
curent Position 17
curent Position Type community
------------ --
beforeCommunity [1, 17, 500, 1]
randValue 11
afterCommunity [1, 17, 500, 1]
------------ --
beforePurchase: [1, 17, 500, 1]
------------ --
roundNumber 6
current PlayerId 2
curent Position 12
curent Position Type utility
------------ --
roundNumber 7
current PlayerId 1
curent Position 22
curent Position Type chance
------

2

Probability of each tile landed

In [17]:
prob_player1 = [1, 0, 500, 0]
prob_player2 = [2, 0, 500, 0]
playerList = [[0, 0 ,99999], prob_player1, prob_player2]
housePurchase = [0] * 40
debugSw = False

In [18]:
count = [0]*40

In [19]:
def gameCountProb(MaxRound = 999999):
    curPlayerId = 1
    roundNumber = 0
    while(MaxRound > 0):
        MaxRound -= 1
        roundNumber += 1
        end = False
        for i in range(len(playerList)):
            if(playerList[i][2] <= 0):
                end = True
                break
        if(end):
            break
        t1 = diceOnce()
        t2 = diceOnce()
        move = t1 + t2
        curPlayer = playerList[curPlayerId]
        posBeforeMove = curPlayer[1]
        curPos = posBeforeMove + move
        curPos = curPos % 40
        debugPrint("------------", "--")
        debugPrint('roundNumber', roundNumber)
        debugPrint('current PlayerId',curPlayerId)
        debugPrint('curent Position',curPos)
        debugPrint('curent Position Type',gameMap[curPos])
        posType = gameDict[gameMap[curPos]][0]
        if(posType == 0):
            playerList[curPlayerId][1] = curPos
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            count[playerList[curPlayerId][1]] += 1;
            continue
        if(posType == 4):
            playerList[curPlayerId][1] = 10
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            count[playerList[curPlayerId][1]] += 1;
            continue
        if(posType == 1):
            playerList[curPlayerId][1] = curPos
            if(housePurchase[curPos] == 0):
                purchase(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                count[playerList[curPlayerId][1]] += 1;
                continue
            if(needRent(playerList[curPlayerId])):
                rent(playerList[curPlayerId])
                curPlayerId = curPlayerId + 1
                if(curPlayerId == len(playerList)):
                    curPlayerId = 1
                count[playerList[curPlayerId][1]] += 1;
                continue
        if(posType == 2):
            playerList[curPlayerId][1] = curPos
            community(playerList[curPlayerId])
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            count[playerList[curPlayerId][1]] += 1;
            continue
        if(posType == 3):
            playerList[curPlayerId][1] = curPos
            chance(playerList[curPlayerId])
            curPlayerId = curPlayerId + 1
            if(curPlayerId == len(playerList)):
                curPlayerId = 1
            count[playerList[curPlayerId][1]] += 1;
            continue
    debugPrint('result', playerList)

In [20]:
gameCountProb(100000000)

In [21]:
print(count)

[3105720, 2154761, 1901425, 2188749, 2349954, 2994531, 2284225, 875154, 2345673, 2332802, 5891710, 2737181, 2627755, 2385061, 2466646, 2918742, 2774918, 2570777, 2915631, 3071076, 2875689, 2828866, 1046046, 2738511, 3189100, 3061690, 2705615, 2678112, 2809002, 2588312, 0, 2684910, 2635111, 2395176, 2507727, 2445962, 873886, 2199620, 2194474, 2649700]


In [22]:
sum(count)

100000000

In [23]:
a = sum(count)
for i in range(len(count)):
    count[i] = count[i]/a
print(count)

[0.0310572, 0.02154761, 0.01901425, 0.02188749, 0.02349954, 0.02994531, 0.02284225, 0.00875154, 0.02345673, 0.02332802, 0.0589171, 0.02737181, 0.02627755, 0.02385061, 0.02466646, 0.02918742, 0.02774918, 0.02570777, 0.02915631, 0.03071076, 0.02875689, 0.02828866, 0.01046046, 0.02738511, 0.031891, 0.0306169, 0.02705615, 0.02678112, 0.02809002, 0.02588312, 0.0, 0.0268491, 0.02635111, 0.02395176, 0.02507727, 0.02445962, 0.00873886, 0.0219962, 0.02194474, 0.026497]


Test for different Strategy

In [31]:
#Comparing only Cheap & only Medium - First Mover only buy cheap
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 1] #only buyCheap
    test_player2 = [2, 0, 500, 2] #only buyMedium
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False

In [32]:
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1

result [[0, 0, 99999], [1, 19, 0, 1], [2, 14, 140, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 10, 200, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 9, 140, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 34, 80, 2]]
result [[0, 0, 99999], [1, 16, 220, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 34, 80, 2]]
result [[0, 0, 99999], [1, 13, 300, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 4, 40, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 33, 280, 2]]
result [[0, 0, 99999], [1, 25, 240, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 15, 240, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 26, 160, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 3, 160, 2]]
result [[0, 0, 99999], [1, 8, 160, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 8, 200, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 12, 180, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 5, 180, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 25, 160, 2]]
result [[0, 0, 99999], [1,

result [[0, 0, 99999], [1, 9, 0, 1], [2, 38, 240, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 29, 80, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 11, 60, 2]]
result [[0, 0, 99999], [1, 26, 80, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 33, 100, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 4, 260, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 13, 160, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 12, 220, 2]]
result [[0, 0, 99999], [1, 25, 220, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 8, 100, 2]]
result [[0, 0, 99999], [1, 35, 40, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 5, 140, 2]]
result [[0, 0, 99999], [1, 16, 280, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 27, 80, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 5, 200, 2]]
result [[0, 0, 99999], [1, 16, 180, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 1, 360, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24, 80, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24,

result [[0, 0, 99999], [1, 26, 0, 1], [2, 4, 180, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 26, 140, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 18, 160, 2]]
result [[0, 0, 99999], [1, 10, 140, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 21, 100, 2]]
result [[0, 0, 99999], [1, 0, 240, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 29, 200, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 15, 140, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 3, 100, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 24, 180, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 5, 160, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 33, 120, 2]]
result [[0, 0, 99999], [1, 34, 160, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 0, 180, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 37, 80, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 21, 40, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 38, 140, 2]]
result [[0, 0, 99999], [1, 33, 80, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 19, 0, 1], [2, 27, 180, 2]]
result [[0, 0, 99999], [1, 25, 320, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 31, 140, 2]]
result [[0, 0, 99999], [1, 9, 180, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 32, 200, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 28, 160, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 32, 180, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 28, 160, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 4, 40, 2]]
result [[0, 0, 99999], [1, 25, 380, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 9, 140, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 17, 220, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 27, 260, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 4, 80, 2]]
result [[0, 0, 99999], [1, 12, 20, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 16, 60, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 10, 100, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 12, 160, 2]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 11, 0, 1], [2, 4, 120, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 39, 240, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 1, 100, 2]]
result [[0, 0, 99999], [1, 14, 360, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 6, 240, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 0, 80, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 5, 80, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 34, 40, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 20, 160, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 16, 80, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 35, 180, 2]]
result [[0, 0, 99999], [1, 29, 340, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 29, 180, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 11, 100, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 23, 80, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 5, 60, 2]]
result [[0, 0, 99999], [1, 25, 280, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 2, 260, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 1

...

result [[0, 0, 99999], [1, 26, 0, 1], [2, 10, 220, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 26, 100, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 24, 180, 2]]
result [[0, 0, 99999], [1, 14, 240, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 23, 420, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 27, 60, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 11, 120, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 38, 140, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 0, 120, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 21, 120, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 2, 240, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 21, 180, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 20, 80, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 24, 180, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 28, 260, 2]]
result [[0, 0, 99999], [1, 21, 60, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 12, 180, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 34, 140, 2]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 16, 0, 1], [2, 20, 180, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 26, 100, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 28, 180, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 8, 260, 2]]
result [[0, 0, 99999], [1, 33, 140, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 39, 60, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 10, 100, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 28, 220, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 15, 160, 2]]
result [[0, 0, 99999], [1, 34, 120, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 25, 180, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 25, 200, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 36, 60, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 32, 80, 2]]
result [[0, 0, 99999], [1, 25, 260, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 4, 40, 2]]
result [[0, 0, 99999], [1, 38, 300, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 5, 160, 2]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 18, 200, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 32, 460, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 36, 140, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 16, 180, 2]]
result [[0, 0, 99999], [1, 29, 280, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 22, 380, 2]]
result [[0, 0, 99999], [1, 0, 320, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 0, 60, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 14, 160, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 7, 140, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 23, 140, 2]]
result [[0, 0, 99999], [1, 35, 80, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 20, 200, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 6, 180, 2]]
result [[0, 0, 99999], [1, 6, 320, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 23, 280, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 0, 160, 2]]
result [[0, 0, 99999], [1, 20, 180, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 

result [[0, 0, 99999], [1, 23, 0, 1], [2, 15, 140, 2]]
result [[0, 0, 99999], [1, 14, 160, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 22, 100, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 39, 140, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 33, 180, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 31, 200, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 21, 220, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 26, 140, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 19, 80, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 0, 140, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 24, 160, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 15, 140, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 0, 220, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 37, 220, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 32, 240, 2]]
result [[0, 0, 99999], [1, 10, 260, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 24, 200, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 34, 60, 2]]
result [[0, 0, 99

result [[0, 0, 99999], [1, 21, 80, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 0, 260, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 9, 60, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 10, 180, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 31, 200, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 0, 120, 2]]
result [[0, 0, 99999], [1, 10, 120, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 28, 140, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 31, 60, 2]]
result [[0, 0, 99999], [1, 27, 220, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 10, 120, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 29, 100, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 19, 200, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 9, 140, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 10, 80, 2]]
result [[0, 0, 99999], [1, 29, 0, 1], [2, 5, 120, 2]]
result [[0, 0, 99999], [1, 19, 40, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 14, 120, 2]]
result [[0, 0, 99999], [1

In [33]:
loseTime

[0, 7102, 2898, 0, 0, 0, 0, 0, 0, 0]

In [34]:
#Comparing only Cheap & only Medium - First Mover only buy medium
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 1] #only buyCheap
    test_player2 = [2, 0, 500, 2] #only buyMedium
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False

In [35]:
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1

result [[0, 0, 99999], [1, 13, 0, 1], [2, 15, 180, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 7, 280, 2]]
result [[0, 0, 99999], [1, 5, 280, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 21, 160, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 26, 100, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 0, 180, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 1, 120, 2]]
result [[0, 0, 99999], [1, 4, 320, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 0, 240, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 32, 220, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 15, 120, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 9, 80, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 10, 300, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 23, 160, 2]]
result [[0, 0, 99999], [1, 23, 120, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 39, 140, 2]]
result [[0, 0, 99999], [1, 10, 240, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 2, 180, 2]]
result [[0, 0, 99999], [1

result [[0, 0, 99999], [1, 24, 0, 1], [2, 21, 120, 2]]
result [[0, 0, 99999], [1, 13, 360, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 32, 80, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 11, 140, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 10, 260, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 32, 160, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 23, 160, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 35, 100, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 25, 100, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 14, 140, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 25, 160, 2]]
result [[0, 0, 99999], [1, 17, 460, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 20, 300, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 33, 120, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 26, 120, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 4, 200, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 21, 160, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 27, 260, 2]]
result [[0, 0, 9

result [[0, 0, 99999], [1, 28, 100, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 33, 260, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 13, 200, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 26, 140, 2]]
result [[0, 0, 99999], [1, 28, 160, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 27, 80, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 25, 220, 2]]
result [[0, 0, 99999], [1, 10, 420, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 17, 80, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 26, 220, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 18, 160, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 15, 140, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 33, 140, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 19, 60, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 37, 80, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 21, 120, 2]]
result [[0, 0, 99999], [1, 35, 260, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 12, 80, 1], [2, 6, 0, 2]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 16, 0, 1], [2, 34, 200, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 8, 120, 2]]
result [[0, 0, 99999], [1, 39, 60, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 0, 200, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 12, 200, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 34, 280, 2]]
result [[0, 0, 99999], [1, 21, 400, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 39, 140, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 9, 100, 2]]
result [[0, 0, 99999], [1, 32, 260, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 13, 200, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 17, 140, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 22, 160, 2]]
result [[0, 0, 99999], [1, 13, 80, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 35, 160, 2]]
result [[0, 0, 99999], [1, 20, 360, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 7, 80, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 26, 80, 2]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 16, 0, 1], [2, 17, 320, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 33, 220, 2]]
result [[0, 0, 99999], [1, 25, 300, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 15, 120, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 38, 120, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 28, 140, 2]]
result [[0, 0, 99999], [1, 29, 0, 1], [2, 16, 160, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 2, 200, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 16, 140, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 18, 180, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 5, 100, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 2, 160, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 37, 340, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 28, 80, 2]]
result [[0, 0, 99999], [1, 10, 220, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 24, 60, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 0, 160, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 10, 100, 2]]
result [[0, 0, 99999

...

result [[0, 0, 99999], [1, 18, 0, 1], [2, 18, 20, 2]]
result [[0, 0, 99999], [1, 31, 420, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 15, 80, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 5, 80, 2]]
result [[0, 0, 99999], [1, 17, 60, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 39, 80, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 2, 120, 2]]
result [[0, 0, 99999], [1, 18, 140, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 29, 0, 1], [2, 38, 160, 2]]
result [[0, 0, 99999], [1, 10, 320, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 15, 180, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 27, 60, 2]]
result [[0, 0, 99999], [1, 7, 360, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 39, 160, 2]]
result [[0, 0, 99999], [1, 17, 220, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 18, 160, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 26, 100, 2]]
result [[0, 0, 99999], [1, 27, 0, 1], [2, 13, 40, 2]]
result [[0, 0, 99999], [1, 

result [[0, 0, 99999], [1, 10, 220, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 20, 140, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 31, 160, 2]]
result [[0, 0, 99999], [1, 10, 160, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 24, 240, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 23, 20, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 14, 160, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 13, 120, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 35, 140, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 35, 100, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 6, 260, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 37, 60, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 5, 200, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 26, 80, 2]]
result [[0, 0, 99999], [1, 10, 420, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 23, 200, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 23, 240, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 39, 300, 2]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 19, 0, 1], [2, 21, 120, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 19, 140, 2]]
result [[0, 0, 99999], [1, 20, 460, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 32, 80, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 10, 240, 2]]
result [[0, 0, 99999], [1, 16, 240, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 11, 120, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 10, 160, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 10, 60, 2]]
result [[0, 0, 99999], [1, 26, 0, 1], [2, 17, 100, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 38, 160, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 10, 180, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 5, 180, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 2, 220, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 8, 120, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 28, 80, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 0, 80, 2]]
result [[0, 0, 99999], [1, 13, 200, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 22, 100, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 10, 200, 2]]
result [[0, 0, 99999], [1, 24, 340, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 32, 300, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 32, 160, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 6, 100, 2]]
result [[0, 0, 99999], [1, 34, 120, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 20, 60, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 23, 80, 1], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 16, 0, 1], [2, 25, 60, 2]]
result [[0, 0, 99999], [1, 12, 320, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 31, 100, 2]]
result [[0, 0, 99999], [1, 13, 320, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 32, 200, 2]]
result [[0, 0, 99999], [1, 5, 360, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 22, 240, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 1, 180, 2]]
result [[0, 0, 99999], [1, 9, 0, 1], [2, 27, 180, 2]]
result [[0, 0, 99999], [1, 26

result [[0, 0, 99999], [1, 21, 0, 1], [2, 25, 180, 2]]
result [[0, 0, 99999], [1, 25, 320, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 19, 260, 1], [2, 1, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 1], [2, 19, 80, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 13, 160, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 3, 140, 2]]
result [[0, 0, 99999], [1, 18, 0, 1], [2, 25, 180, 2]]
result [[0, 0, 99999], [1, 23, 0, 1], [2, 6, 120, 2]]
result [[0, 0, 99999], [1, 10, 200, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 1], [2, 25, 160, 2]]
result [[0, 0, 99999], [1, 13, 0, 1], [2, 28, 20, 2]]
result [[0, 0, 99999], [1, 26, 140, 1], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 11, 120, 2]]
result [[0, 0, 99999], [1, 14, 0, 1], [2, 19, 140, 2]]
result [[0, 0, 99999], [1, 21, 0, 1], [2, 15, 160, 2]]
result [[0, 0, 99999], [1, 24, 0, 1], [2, 33, 60, 2]]
result [[0, 0, 99999], [1, 18, 300, 1], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 29, 0, 1], [2, 17, 80, 2]]
result [[0, 0, 99999]

In [36]:
loseTime

[0, 7101, 2899, 0, 0, 0, 0, 0, 0, 0]

In [37]:
#Comparing only Cheap & only Expensive - First Mover only buy Cheap
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 1] #only buy Cheap
    test_player2 = [2, 0, 500, 3] #only buy Expensive
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False

In [38]:
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1

result [[0, 0, 99999], [1, 32, 0, 1], [2, 32, 80, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 6, 240, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 27, 90, 3]]
result [[0, 0, 99999], [1, 21, 420, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 0, 170, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 8, 220, 3]]
result [[0, 0, 99999], [1, 12, 380, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 5, 280, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 10, 380, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 35, 220, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 29, 80, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 12, 140, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 4, 140, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 9, 140, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 28, 230, 3]]
result [[0, 0, 99999], [1, 8, 180, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 20, 140, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 39, 360, 3]]
result [[0, 0, 99999], [1, 37,

result [[0, 0, 99999], [1, 31, 0, 1], [2, 34, 140, 3]]
result [[0, 0, 99999], [1, 37, 220, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 5, 330, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 3, 90, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 29, 160, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 24, 340, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 15, 360, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 35, 480, 3]]
result [[0, 0, 99999], [1, 25, 380, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 14, 220, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 29, 130, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 16, 280, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 13, 120, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 0, 520, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 39, 130, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 32, 380, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 17, 250, 3]]
result [[0, 0, 99999], [1, 21, 170, 1], [2, 6, 0, 3]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 11, 280, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 18, 330, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 16, 180, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 10, 380, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 27, 220, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 18, 300, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 16, 380, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 29, 240, 3]]
result [[0, 0, 99999], [1, 31, 340, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 4, 80, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 2, 380, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 10, 360, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 6, 360, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 19, 120, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 14, 380, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 5, 420, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 9, 390, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 8, 180, 3]]
result [[0, 0, 9999

result [[0, 0, 99999], [1, 37, 80, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 33, 220, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 35, 380, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 19, 140, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 2, 160, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 4, 440, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 18, 240, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 9, 380, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 4, 280, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 14, 380, 3]]
result [[0, 0, 99999], [1, 4, 270, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 10, 90, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 16, 360, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 24, 360, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 18, 340, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 15, 280, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 0, 220, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 3, 160, 3]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 34, 0, 1], [2, 11, 360, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 17, 420, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 11, 330, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 34, 290, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 35, 340, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 38, 120, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 10, 220, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 0, 220, 3]]
result [[0, 0, 99999], [1, 16, 160, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 20, 300, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 32, 60, 3]]
result [[0, 0, 99999], [1, 16, 140, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 16, 120, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 37, 460, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 10, 280, 3]]
result [[0, 0, 99999], [1, 37, 80, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 38, 240, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 13, 380, 3]]
result [[0, 0, 9

...

result [[0, 0, 99999], [1, 7, 360, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 19, 80, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 6, 380, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 39, 360, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 39, 150, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 19, 120, 3]]
result [[0, 0, 99999], [1, 11, 330, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 18, 340, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 34, 180, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 10, 380, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 23, 110, 3]]
result [[0, 0, 99999], [1, 11, 80, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 5, 380, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 38, 240, 3]]
result [[0, 0, 99999], [1, 4, 140, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 35, 360, 3]]
result [[0, 0, 99999], [1, 11, 380, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 13, 390, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 32, 0, 1], [2, 26, 220, 3]]
result [[0, 0, 99999], [1, 24, 420, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 28, 440, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 13, 220, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 21, 210, 3]]
result [[0, 0, 99999], [1, 27, 220, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 1, 250, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 38, 360, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 7, 220, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 19, 340, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 28, 220, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 1, 340, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 34, 380, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 4, 140, 3]]
result [[0, 0, 99999], [1, 25, 220, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 12, 390, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 10, 180, 3]]
result [[0, 0, 99999], [1, 0, 60, 1], [2, 1, 0, 3]]
result [[0, 0, 99999

result [[0, 0, 99999], [1, 34, 0, 1], [2, 24, 60, 3]]
result [[0, 0, 99999], [1, 8, 60, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 31, 340, 3]]
result [[0, 0, 99999], [1, 39, 300, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 2, 280, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 29, 190, 3]]
result [[0, 0, 99999], [1, 37, 0, 1], [2, 21, 250, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 38, 140, 3]]
result [[0, 0, 99999], [1, 20, 80, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 21, 30, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 19, 180, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 10, 440, 3]]
result [[0, 0, 99999], [1, 38, 120, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 5, 150, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 20, 380, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 19, 140, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 15, 400, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 18, 340, 3]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 31, 0, 1], [2, 33, 340, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 7, 120, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 22, 380, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 6, 380, 3]]
result [[0, 0, 99999], [1, 26, 330, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 19, 380, 3]]
result [[0, 0, 99999], [1, 2, 140, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 24, 90, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 28, 360, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 6, 160, 3]]
result [[0, 0, 99999], [1, 39, 0, 1], [2, 13, 380, 3]]
result [[0, 0, 99999], [1, 27, 380, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 16, 280, 3]]
result [[0, 0, 99999], [1, 33, 320, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 1, 160, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 26, 380, 3]]
result [[0, 0, 99999], [1, 36, 160, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 1, 360, 3]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 34, 0, 1], [2, 29, 360, 3]]
result [[0, 0, 99999], [1, 19, 360, 1], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 2, 380, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 19, 140, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 35, 160, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 24, 130, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 26, 220, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 9, 380, 3]]
result [[0, 0, 99999], [1, 20, 280, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 24, 190, 3]]
result [[0, 0, 99999], [1, 32, 0, 1], [2, 25, 80, 3]]
result [[0, 0, 99999], [1, 31, 0, 1], [2, 15, 160, 3]]
result [[0, 0, 99999], [1, 10, 60, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 35, 280, 1], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 21, 140, 1], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 1], [2, 35, 160, 3]]
result [[0, 0, 99999], [1, 29, 80, 1], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 18, 360, 1], [2, 8, 0, 3]]
result [[0, 0, 99999],

In [39]:
loseTime

[0, 7246, 2754, 0, 0, 0, 0, 0, 0, 0]

In [40]:
#Comparing only Cheap & only Expensive - First Mover only buy Cheap
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 3] #only buy Cheap
    test_player2 = [2, 0, 500, 1] #only buy Expensive
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False

In [41]:
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1

result [[0, 0, 99999], [1, 8, 0, 3], [2, 18, 120, 1]]
result [[0, 0, 99999], [1, 29, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 36, 300, 1]]
result [[0, 0, 99999], [1, 28, 280, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 15, 220, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 37, 180, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 29, 300, 1]]
result [[0, 0, 99999], [1, 34, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 8, 60, 1]]
result [[0, 0, 99999], [1, 33, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 12, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 26, 60, 1]]
result [[0, 0, 99999], [1, 23, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 11, 80, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 1, 0, 3], [2, 28, 60, 1]]
result [[0, 0, 99999], [1, 31, 190, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 36, 80, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 21, 120, 3], [2, 34, 0, 1]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 19, 280, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 32, 160, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 19, 280, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 37, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 22, 340, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 28, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 20, 280, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 32, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 15, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 29, 540, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 10, 360, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 33, 280, 1]]
result [[0, 0, 99999], [1, 15, 280, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 3], [2, 11, 80, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 5, 330, 1]]
result [[0, 0, 99999], [1, 4, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 38, 90, 1]]
result [[0, 0, 99999], [1, 2, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999

result [[0, 0, 99999], [1, 8, 0, 3], [2, 23, 380, 1]]
result [[0, 0, 99999], [1, 39, 390, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 3], [2, 27, 30, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 27, 60, 1]]
result [[0, 0, 99999], [1, 25, 220, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 33, 60, 1]]
result [[0, 0, 99999], [1, 10, 160, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 10, 80, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 34, 160, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 38, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 7, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 2, 380, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 9, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 9, 160, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 28, 60, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 11, 540, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 38, 430, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 39, 180, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 8, 0, 3], [2, 31, 380, 1]]
result [[0, 0, 99999], [1, 24, 120, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 21, 430, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 26, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 20, 220, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 26, 220, 1]]
result [[0, 0, 99999], [1, 13, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 12, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 1, 180, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 34, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 19, 160, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 10, 160, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 17, 80, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 35, 380, 1]]
result [[0, 0, 99999], [1, 29, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 0, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 26, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 24, 420, 3], [2, 34, 0, 1]]
result [[0, 0, 9

result [[0, 0, 99999], [1, 19, 60, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 39, 140, 1]]
result [[0, 0, 99999], [1, 5, 320, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 15, 90, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 9, 120, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 3, 120, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 34, 130, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 5, 280, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 25, 280, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 21, 420, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 3, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 11, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 10, 160, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 3], [2, 12, 280, 1]]
result [[0, 0, 99999], [1, 1, 0, 3], [2, 12, 360, 1]]
result [[0, 0, 99999], [1, 9, 220, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 26, 330, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 20, 220, 1]]
result [[0, 0, 99999], 

...

result [[0, 0, 99999], [1, 11, 120, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 20, 280, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 0, 160, 1]]
result [[0, 0, 99999], [1, 14, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 0, 280, 1]]
result [[0, 0, 99999], [1, 35, 340, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 21, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 5, 490, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 38, 280, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 17, 360, 1]]
result [[0, 0, 99999], [1, 38, 180, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 16, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 19, 190, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 0, 280, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 1, 0, 3], [2, 15, 220, 1]]
result [[0, 0, 99999], [1, 33, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 3], [2, 22, 80, 1]]
result [[0, 0, 99999], [1, 0, 440, 3], [2, 31, 0, 1]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 6, 0, 3], [2, 24, 380, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 28, 200, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 19, 80, 1]]
result [[0, 0, 99999], [1, 26, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 35, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 26, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 19, 160, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 10, 190, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 3], [2, 25, 330, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 1, 240, 1]]
result [[0, 0, 99999], [1, 2, 440, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 15, 120, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 24, 100, 1]]
result [[0, 0, 99999], [1, 28, 180, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 15, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 4, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 2, 60, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 34, 120, 3], [2, 34, 0, 1]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 3, 380, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 10, 280, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 28, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 4, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 3], [2, 22, 180, 1]]
result [[0, 0, 99999], [1, 25, 140, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 1, 0, 3], [2, 38, 160, 1]]
result [[0, 0, 99999], [1, 34, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 26, 60, 1]]
result [[0, 0, 99999], [1, 0, 160, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 26, 140, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 14, 540, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 0, 90, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 33, 140, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 19, 60, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 20, 420, 1]]
result [[0, 0, 99999], [1, 35, 280, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 14, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 32, 220, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 31, 180, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 16, 90, 1]]
result [[0, 0, 99999], [1, 3, 340, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 20, 60, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 29, 120, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 19, 220, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 23, 190, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 29, 340, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 7, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 10, 440, 1]]
result [[0, 0, 99999], [1, 25, 160, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 18, 330, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 7, 220, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 13, 120, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 20, 220, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 10, 80, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 19, 190, 3], [2, 32, 0, 1]]
result [[0, 0, 999

result [[0, 0, 99999], [1, 8, 0, 3], [2, 8, 220, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 27, 220, 1]]
result [[0, 0, 99999], [1, 36, 160, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 4, 320, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 4, 380, 1]]
result [[0, 0, 99999], [1, 17, 160, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 36, 360, 3], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 21, 220, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 16, 380, 3], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 27, 390, 3], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 10, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 3], [2, 33, 30, 1]]
result [[0, 0, 99999], [1, 0, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 16, 80, 3], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 34, 340, 3], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 3], [2, 10, 160, 1]]
result [[0, 0, 99999], [1, 1, 0, 3], [2, 11, 220, 1]]
result [[0, 0, 99999], [1, 25, 380, 3], [2, 31, 0, 1]]
result [[0, 0, 99999],

In [42]:
loseTime

[0, 2761, 7239, 0, 0, 0, 0, 0, 0, 0]

In [17]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 1] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 10, 320, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 27, 60, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 20, 40, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 2, 120, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 21, 200, 7], [2, 8, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 27, 380, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 23, 260, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 5, 60, 1]]
result [[0, 0, 99999], [1, 20, 220, 7], [2, 19, 0, 1]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 34, 0, 1]]
result [[0, 0, 99999], [1, 24, 60, 7], [2, 1, 0, 1]]
result [[0, 0, 99999], [1, 10, 200, 7], [2, 13, 0, 1]]
result [[0, 0, 99999], [1, 10, 220, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 28, 200, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 38, 140, 7], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 16, 40, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 33, 320, 1]]
result [[0, 0, 99999], [1, 21, 80, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1,

result [[0, 0, 99999], [1, 31, 60, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 11, 260, 1]]
result [[0, 0, 99999], [1, 24, 80, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 5, 140, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 0, 300, 1]]
result [[0, 0, 99999], [1, 35, 200, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 12, 230, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 10, 180, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 25, 120, 7], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 25, 360, 1]]
result [[0, 0, 99999], [1, 10, 200, 7], [2, 23, 0, 1]]
result [[0, 0, 99999], [1, 27, 200, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 24, 260, 1]]
result [[0, 0, 99999], [1, 18, 60, 7], [2, 24, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 17, 160, 1]]
result [[0, 0, 99999], [1, 15, 180, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 31, 40, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 10, 160, 1]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 23, 120, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 39, 240, 7], [2, 3, 0, 1]]
result [[0, 0, 99999], [1, 5, 120, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 4, 200, 7], [2, 13, 0, 1]]
result [[0, 0, 99999], [1, 38, 120, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 24, 240, 7], [2, 29, 0, 1]]
result [[0, 0, 99999], [1, 28, 200, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 17, 260, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 9, 120, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 26, 160, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 2, 200, 1]]
result [[0, 0, 99999], [1, 31, 180, 7], [2, 24, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 28, 60, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 23, 300, 1]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 1, 100, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 10, 360, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 34, 180, 1]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 3, 0, 7], [2, 31, 380, 1]]
result [[0, 0, 99999], [1, 34, 240, 7], [2, 31, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 16, 160, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 3, 20, 1]]
result [[0, 0, 99999], [1, 0, 180, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 37, 220, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 19, 100, 7], [2, 13, 0, 1]]
result [[0, 0, 99999], [1, 5, 320, 7], [2, 8, 0, 1]]
result [[0, 0, 99999], [1, 39, 160, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 14, 200, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 38, 40, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 24, 100, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 26, 220, 1]]
result [[0, 0, 99999], [1, 28, 200, 7], [2, 23, 0, 1]]
result [[0, 0, 99999], [1, 25, 80, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 13, 180, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 10, 240, 1]]
result [[0, 0, 99999], [1, 11, 200, 7], [2, 23, 0, 1]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 3, 0, 7], [2, 10, 60, 1]]
result [[0, 0, 99999], [1, 18, 160, 7], [2, 24, 0, 1]]
result [[0, 0, 99999], [1, 17, 40, 7], [2, 3, 0, 1]]
result [[0, 0, 99999], [1, 27, 160, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 37, 40, 7], [2, 3, 0, 1]]
result [[0, 0, 99999], [1, 32, 60, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 17, 120, 7], [2, 19, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 24, 400, 1]]
result [[0, 0, 99999], [1, 1, 0, 7], [2, 31, 220, 1]]
result [[0, 0, 99999], [1, 12, 220, 7], [2, 26, 0, 1]]
result [[0, 0, 99999], [1, 36, 20, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 17, 420, 1]]
result [[0, 0, 99999], [1, 24, 180, 7], [2, 13, 0, 1]]
result [[0, 0, 99999], [1, 12, 240, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 31, 100, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 35, 460, 1]]
result [[0, 0, 99999], [1, 24, 180, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 31, 240, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1

...

result [[0, 0, 99999], [1, 8, 0, 7], [2, 2, 60, 1]]
result [[0, 0, 99999], [1, 14, 30, 7], [2, 37, 0, 1]]
result [[0, 0, 99999], [1, 26, 40, 7], [2, 8, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 22, 260, 1]]
result [[0, 0, 99999], [1, 2, 180, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 37, 340, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 12, 300, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 23, 320, 1]]
result [[0, 0, 99999], [1, 39, 160, 7], [2, 26, 0, 1]]
result [[0, 0, 99999], [1, 18, 40, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 1, 0, 7], [2, 7, 40, 1]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 19, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 4, 120, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 21, 100, 1]]
result [[0, 0, 99999], [1, 35, 160, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 14, 220, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 7, 160, 7], [2, 27, 0, 1]]
result [[0, 0, 99999], [1, 16, 140, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 6,

result [[0, 0, 99999], [1, 8, 0, 7], [2, 27, 180, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 29, 420, 1]]
result [[0, 0, 99999], [1, 4, 240, 7], [2, 39, 0, 1]]
result [[0, 0, 99999], [1, 18, 120, 7], [2, 13, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 19, 400, 1]]
result [[0, 0, 99999], [1, 0, 160, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 37, 80, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 18, 100, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 24, 320, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 29, 120, 1]]
result [[0, 0, 99999], [1, 15, 140, 7], [2, 23, 0, 1]]
result [[0, 0, 99999], [1, 3, 120, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 15, 320, 1]]
result [[0, 0, 99999], [1, 28, 160, 7], [2, 24, 0, 1]]
result [[0, 0, 99999], [1, 19, 120, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 4, 100, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 9, 60, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 11, 120, 7], [2, 26, 0, 1]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 11, 160, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 37, 200, 7], [2, 23, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 7, 180, 1]]
result [[0, 0, 99999], [1, 13, 100, 7], [2, 32, 0, 1]]
result [[0, 0, 99999], [1, 27, 220, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 39, 360, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 20, 360, 1]]
result [[0, 0, 99999], [1, 31, 220, 7], [2, 23, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 39, 340, 1]]
result [[0, 0, 99999], [1, 1, 0, 7], [2, 4, 320, 1]]
result [[0, 0, 99999], [1, 26, 80, 7], [2, 19, 0, 1]]
result [[0, 0, 99999], [1, 0, 180, 7], [2, 24, 0, 1]]
result [[0, 0, 99999], [1, 10, 200, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 24, 180, 1]]
result [[0, 0, 99999], [1, 7, 160, 7], [2, 19, 0, 1]]
result [[0, 0, 99999], [1, 6, 280, 7], [2, 27, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 25, 260, 1]]
result [[0, 0, 99999], [1, 26, 160, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 20, 200, 7], [2, 21, 0, 1]]
result [[0, 0, 99999], [1, 5, 140, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 9, 160, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 20, 80, 7], [2, 8, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 21, 140, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 13, 180, 1]]
result [[0, 0, 99999], [1, 1, 0, 7], [2, 11, 40, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 15, 380, 1]]
result [[0, 0, 99999], [1, 24, 120, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 21, 140, 7], [2, 29, 0, 1]]
result [[0, 0, 99999], [1, 16, 60, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 24, 80, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 4, 180, 7], [2, 27, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 10, 400, 1]]
result [[0, 0, 99999], [1, 32, 60, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 16, 40, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 16, 120, 7], [2, 6, 0, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 18, 40, 1]]
result [[0, 0, 99999], [1, 1, 0

result [[0, 0, 99999], [1, 19, 100, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 0, 120, 7], [2, 26, 0, 1]]
result [[0, 0, 99999], [1, 20, 40, 7], [2, 3, 0, 1]]
result [[0, 0, 99999], [1, 5, 140, 7], [2, 18, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 28, 420, 1]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 19, 280, 1]]
result [[0, 0, 99999], [1, 20, 40, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 4, 200, 7], [2, 16, 0, 1]]
result [[0, 0, 99999], [1, 19, 100, 7], [2, 9, 0, 1]]
result [[0, 0, 99999], [1, 26, 200, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 3, 60, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 28, 200, 7], [2, 14, 0, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 10, 300, 1]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 5, 260, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 33, 340, 1]]
result [[0, 0, 99999], [1, 19, 20, 7], [2, 19, 0, 1]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 25, 440, 1]]
result [[0, 0, 99999], [1, 18, 80, 7], [2, 11, 0, 1]]
result [[0, 0, 99999], [1, 8

In [18]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 2] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 18, 0, 7], [2, 0, 120, 2]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 33, 80, 2]]
result [[0, 0, 99999], [1, 27, 60, 7], [2, 26, 0, 2]]
result [[0, 0, 99999], [1, 31, 140, 7], [2, 32, 0, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 17, 140, 2]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 12, 160, 2]]
result [[0, 0, 99999], [1, 10, 60, 7], [2, 14, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 8, 120, 2]]
result [[0, 0, 99999], [1, 11, 120, 7], [2, 23, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 39, 240, 2]]
result [[0, 0, 99999], [1, 2, 140, 7], [2, 23, 0, 2]]
result [[0, 0, 99999], [1, 26, 120, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 9, 70, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 39, 100, 2]]
result [[0, 0, 99999], [1, 33, 80, 7], [2, 9, 0, 2]]
result [[0, 0, 99999], [1, 17, 80, 7], [2, 18, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 32, 180, 2]]
result [[0, 0, 99999], [1, 18, 220, 7], [2, 29, 0, 2]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 16, 80, 7], [2, 14, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 10, 100, 2]]
result [[0, 0, 99999], [1, 31, 100, 7], [2, 9, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 26, 160, 2]]
result [[0, 0, 99999], [1, 25, 120, 7], [2, 27, 0, 2]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 35, 180, 2]]
result [[0, 0, 99999], [1, 19, 140, 7], [2, 26, 0, 2]]
result [[0, 0, 99999], [1, 21, 80, 7], [2, 13, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 25, 60, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 20, 100, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 36, 100, 2]]
result [[0, 0, 99999], [1, 32, 160, 7], [2, 24, 0, 2]]
result [[0, 0, 99999], [1, 0, 200, 7], [2, 26, 0, 2]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 28, 60, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 5, 140, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 12, 100, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 31, 120, 2]]
result [[0, 0, 99999], [1, 25, 160, 7], [2, 14, 0, 2]]
result [[0, 0, 99

result [[0, 0, 99999], [1, 8, 120, 7], [2, 18, 0, 2]]
result [[0, 0, 99999], [1, 15, 120, 7], [2, 11, 0, 2]]
result [[0, 0, 99999], [1, 23, 100, 7], [2, 31, 0, 2]]
result [[0, 0, 99999], [1, 0, 140, 7], [2, 14, 0, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 39, 100, 2]]
result [[0, 0, 99999], [1, 0, 220, 7], [2, 21, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 23, 80, 2]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 36, 40, 2]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 10, 220, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 19, 140, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 5, 140, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 23, 120, 2]]
result [[0, 0, 99999], [1, 18, 160, 7], [2, 24, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 0, 140, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 0, 100, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 27, 100, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 26, 100, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 0, 100, 2]]
result [[0, 0, 99999

result [[0, 0, 99999], [1, 13, 0, 7], [2, 24, 180, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 27, 100, 2]]
result [[0, 0, 99999], [1, 8, 40, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 39, 60, 2]]
result [[0, 0, 99999], [1, 6, 100, 7], [2, 18, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 16, 180, 2]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 19, 20, 2]]
result [[0, 0, 99999], [1, 23, 80, 7], [2, 14, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 33, 60, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 10, 60, 2]]
result [[0, 0, 99999], [1, 17, 220, 7], [2, 39, 0, 2]]
result [[0, 0, 99999], [1, 25, 60, 7], [2, 23, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 29, 60, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 7, 200, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 10, 200, 2]]
result [[0, 0, 99999], [1, 17, 40, 7], [2, 32, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 13, 140, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 21, 180, 2]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 10, 140, 7], [2, 23, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 32, 200, 2]]
result [[0, 0, 99999], [1, 12, 80, 7], [2, 26, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 13, 120, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 3, 140, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 39, 140, 2]]
result [[0, 0, 99999], [1, 36, 60, 7], [2, 23, 0, 2]]
result [[0, 0, 99999], [1, 25, 100, 7], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 15, 140, 2]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 39, 280, 2]]
result [[0, 0, 99999], [1, 1, 100, 7], [2, 9, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 8, 140, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 20, 140, 2]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 31, 160, 2]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 33, 220, 2]]
result [[0, 0, 99999], [1, 25, 220, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 32, 40, 2]]
result [[0, 0, 99999], [1, 10, 80, 7], [2, 3, 0, 2]]
result [[0, 0, 99999]

...

result [[0, 0, 99999], [1, 24, 0, 7], [2, 9, 160, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 39, 60, 2]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 32, 160, 2]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 27, 160, 2]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 18, 160, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 28, 120, 2]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 3, 140, 2]]
result [[0, 0, 99999], [1, 17, 40, 7], [2, 14, 0, 2]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 35, 120, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 25, 220, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 2, 40, 2]]
result [[0, 0, 99999], [1, 9, 100, 7], [2, 11, 0, 2]]
result [[0, 0, 99999], [1, 5, 140, 7], [2, 23, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 3, 80, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 8, 60, 2]]
result [[0, 0, 99999], [1, 28, 220, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 23, 120, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 4, 160, 2]]
result [[0, 0, 99999], [1, 

result [[0, 0, 99999], [1, 26, 0, 7], [2, 35, 140, 2]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 36, 60, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 25, 200, 2]]
result [[0, 0, 99999], [1, 11, 120, 7], [2, 27, 0, 2]]
result [[0, 0, 99999], [1, 32, 100, 7], [2, 16, 0, 2]]
result [[0, 0, 99999], [1, 2, 40, 7], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 12, 60, 7], [2, 16, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 26, 80, 2]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 39, 100, 2]]
result [[0, 0, 99999], [1, 24, 220, 7], [2, 27, 0, 2]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 35, 220, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 28, 160, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 9, 120, 2]]
result [[0, 0, 99999], [1, 28, 100, 7], [2, 14, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 22, 320, 2]]
result [[0, 0, 99999], [1, 18, 200, 7], [2, 13, 0, 2]]
result [[0, 0, 99999], [1, 20, 100, 7], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 15, 160, 2]]
result [[0, 0, 9999

result [[0, 0, 99999], [1, 37, 40, 7], [2, 8, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 5, 40, 2]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 38, 80, 2]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 15, 60, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 4, 300, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 14, 220, 2]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 21, 140, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 29, 160, 2]]
result [[0, 0, 99999], [1, 2, 80, 7], [2, 9, 0, 2]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 16, 180, 2]]
result [[0, 0, 99999], [1, 9, 40, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 20, 100, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 10, 100, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 15, 100, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 8, 80, 2]]
result [[0, 0, 99999], [1, 33, 60, 7], [2, 32, 0, 2]]
result [[0, 0, 99999], [1, 20, 140, 7], [2, 16, 0, 2]]
result [[0, 0, 99999], [1, 32, 120, 7], [2, 18, 0, 2]]
result [[0, 0, 99999], [1

result [[0, 0, 99999], [1, 34, 180, 7], [2, 11, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 8, 40, 2]]
result [[0, 0, 99999], [1, 34, 140, 7], [2, 6, 0, 2]]
result [[0, 0, 99999], [1, 15, 140, 7], [2, 21, 0, 2]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 29, 180, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 31, 140, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 39, 60, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 23, 80, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 13, 120, 2]]
result [[0, 0, 99999], [1, 13, 180, 7], [2, 16, 0, 2]]
result [[0, 0, 99999], [1, 13, 60, 7], [2, 24, 0, 2]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 31, 120, 2]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 3, 200, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 8, 40, 2]]
result [[0, 0, 99999], [1, 35, 40, 7], [2, 21, 0, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 25, 180, 2]]
result [[0, 0, 99999], [1, 19, 140, 7], [2, 29, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 35, 120, 2]]
result [[0, 0, 99999

result [[0, 0, 99999], [1, 18, 0, 7], [2, 32, 180, 2]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 24, 160, 2]]
result [[0, 0, 99999], [1, 25, 80, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 15, 200, 2]]
result [[0, 0, 99999], [1, 3, 100, 7], [2, 19, 0, 2]]
result [[0, 0, 99999], [1, 12, 100, 7], [2, 18, 0, 2]]
result [[0, 0, 99999], [1, 10, 60, 7], [2, 3, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 10, 320, 2]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 21, 200, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 20, 120, 2]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 35, 140, 2]]
result [[0, 0, 99999], [1, 13, 100, 7], [2, 16, 0, 2]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 34, 200, 2]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 0, 200, 2]]
result [[0, 0, 99999], [1, 26, 200, 7], [2, 11, 0, 2]]
result [[0, 0, 99999], [1, 14, 60, 7], [2, 18, 0, 2]]
result [[0, 0, 99999], [1, 6, 100, 7], [2, 24, 0, 2]]
result [[0, 0, 99999], [1, 35, 140, 7], [2, 27, 0, 2]]
result [[0, 0, 99

In [19]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 3] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 34, 0, 7], [2, 19, 160, 3]]
result [[0, 0, 99999], [1, 17, 100, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 39, 260, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 13, 220, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 9, 130, 3]]
result [[0, 0, 99999], [1, 17, 100, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 160, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 7, 180, 3]]
result [[0, 0, 99999], [1, 32, 190, 7], [2, 21, 0, 3]]
result [[0, 0, 99999], [1, 28, 60, 7], [2, 9, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 25, 110, 3]]
result [[0, 0, 99999], [1, 32, 120, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 3, 220, 3]]
result [[0, 0, 99999], [1, 20, 120, 7], [2, 13, 0, 3]]
result [[0, 0, 99999], [1, 38, 40, 7], [2, 26, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 38, 40, 3]]
result [[0, 0, 99999], [1, 5, 320, 7], [2, 24, 0, 3]]
result [[0, 0, 99999], [1, 1, 180, 7], [2, 14, 0, 3]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 19, 160, 7], [2, 31, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 26, 220, 3]]
result [[0, 0, 99999], [1, 1, 140, 7], [2, 16, 0, 3]]
result [[0, 0, 99999], [1, 31, 280, 7], [2, 14, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 10, 320, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 2, 120, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 4, 280, 3]]
result [[0, 0, 99999], [1, 39, 160, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 10, 60, 7], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 19, 120, 3]]
result [[0, 0, 99999], [1, 17, 160, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 10, 240, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 14, 200, 3]]
result [[0, 0, 99999], [1, 10, 40, 7], [2, 9, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 26, 180, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 23, 340, 3]]
result [[0, 0, 99999], [1, 23, 140, 7], [2, 13, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 31, 140, 3]]
result [[0, 0, 99

result [[0, 0, 99999], [1, 31, 0, 7], [2, 18, 240, 3]]
result [[0, 0, 99999], [1, 27, 160, 7], [2, 11, 0, 3]]
result [[0, 0, 99999], [1, 4, 180, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 37, 150, 3]]
result [[0, 0, 99999], [1, 1, 90, 7], [2, 11, 0, 3]]
result [[0, 0, 99999], [1, 0, 160, 7], [2, 16, 0, 3]]
result [[0, 0, 99999], [1, 0, 240, 7], [2, 39, 0, 3]]
result [[0, 0, 99999], [1, 8, 60, 7], [2, 24, 0, 3]]
result [[0, 0, 99999], [1, 0, 120, 7], [2, 9, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 20, 140, 3]]
result [[0, 0, 99999], [1, 18, 120, 7], [2, 13, 0, 3]]
result [[0, 0, 99999], [1, 8, 120, 7], [2, 24, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 36, 160, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 17, 220, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 18, 220, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 31, 240, 3]]
result [[0, 0, 99999], [1, 12, 120, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 12, 220, 3]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 32, 0, 7], [2, 11, 220, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 6, 120, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 0, 260, 3]]
result [[0, 0, 99999], [1, 29, 40, 7], [2, 13, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 25, 360, 3]]
result [[0, 0, 99999], [1, 16, 120, 7], [2, 29, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 16, 160, 3]]
result [[0, 0, 99999], [1, 20, 60, 7], [2, 11, 0, 3]]
result [[0, 0, 99999], [1, 13, 120, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 27, 180, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 25, 40, 7], [2, 21, 0, 3]]
result [[0, 0, 99999], [1, 10, 100, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 23, 120, 7], [2, 24, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 2, 240, 3]]
result [[0, 0, 99999], [1, 32, 120, 7], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 9, 300, 7], [2, 39, 0, 3]]
result [[0, 0, 99999], [1, 31, 60, 7], [2, 3, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 35, 180, 3]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 37, 0, 7], [2, 10, 170, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 23, 40, 3]]
result [[0, 0, 99999], [1, 28, 160, 7], [2, 27, 0, 3]]
result [[0, 0, 99999], [1, 31, 80, 7], [2, 29, 0, 3]]
result [[0, 0, 99999], [1, 35, 40, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 39, 200, 7], [2, 21, 0, 3]]
result [[0, 0, 99999], [1, 15, 60, 7], [2, 24, 0, 3]]
result [[0, 0, 99999], [1, 27, 40, 7], [2, 11, 0, 3]]
result [[0, 0, 99999], [1, 16, 60, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 31, 140, 7], [2, 16, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 6, 240, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 3, 360, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 3, 150, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 5, 320, 3]]
result [[0, 0, 99999], [1, 15, 100, 7], [2, 23, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 28, 140, 3]]
result [[0, 0, 99999], [1, 27, 130, 7], [2, 13, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 13, 100, 3]]
result [[0, 0, 99999

...

result [[0, 0, 99999], [1, 33, 100, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 33, 280, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 0, 200, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 14, 220, 3]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 27, 280, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 1, 240, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 23, 220, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 13, 80, 3]]
result [[0, 0, 99999], [1, 10, 110, 7], [2, 23, 0, 3]]
result [[0, 0, 99999], [1, 15, 120, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 26, 240, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 20, 220, 3]]
result [[0, 0, 99999], [1, 33, 80, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 19, 130, 7], [2, 16, 0, 3]]
result [[0, 0, 99999], [1, 31, 130, 7], [2, 9, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 35, 190, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 20, 140, 3]]
result [[0, 0, 999

result [[0, 0, 99999], [1, 4, 140, 7], [2, 11, 0, 3]]
result [[0, 0, 99999], [1, 13, 120, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 18, 120, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 17, 240, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 22, 80, 3]]
result [[0, 0, 99999], [1, 13, 80, 7], [2, 29, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 39, 120, 3]]
result [[0, 0, 99999], [1, 16, 160, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 27, 240, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 33, 80, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 24, 160, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 25, 220, 3]]
result [[0, 0, 99999], [1, 39, 160, 7], [2, 34, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 28, 80, 3]]
result [[0, 0, 99999], [1, 35, 140, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 32, 220, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 29, 120, 7], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 11, 240, 7], [2, 39, 0, 3]]
result [[0, 0, 99

result [[0, 0, 99999], [1, 37, 0, 7], [2, 34, 190, 3]]
result [[0, 0, 99999], [1, 8, 100, 7], [2, 11, 0, 3]]
result [[0, 0, 99999], [1, 21, 300, 7], [2, 39, 0, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 25, 130, 3]]
result [[0, 0, 99999], [1, 10, 140, 7], [2, 6, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 37, 220, 3]]
result [[0, 0, 99999], [1, 27, 60, 7], [2, 31, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 14, 160, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 17, 180, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 39, 200, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 16, 360, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 8, 280, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 13, 190, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 14, 170, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 18, 200, 3]]
result [[0, 0, 99999], [1, 0, 60, 7], [2, 32, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 19, 160, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 38, 240, 3]]
result [[0, 0, 9

result [[0, 0, 99999], [1, 15, 160, 7], [2, 27, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 0, 60, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 15, 280, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 33, 160, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 0, 180, 3]]
result [[0, 0, 99999], [1, 27, 40, 7], [2, 19, 0, 3]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 21, 160, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 33, 160, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 10, 130, 3]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 23, 0, 3]]
result [[0, 0, 99999], [1, 0, 140, 7], [2, 1, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 0, 120, 3]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 16, 0, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 10, 240, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 19, 280, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 16, 180, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 11, 240, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 28, 100, 3]]
result [[0, 0, 99

result [[0, 0, 99999], [1, 31, 0, 7], [2, 8, 120, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 8, 110, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 18, 240, 3]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 4, 260, 3]]
result [[0, 0, 99999], [1, 10, 120, 7], [2, 18, 0, 3]]
result [[0, 0, 99999], [1, 8, 90, 7], [2, 8, 0, 3]]
result [[0, 0, 99999], [1, 2, 140, 7], [2, 14, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 3, 100, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 14, 220, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 2, 220, 3]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 0, 240, 3]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 4, 220, 3]]
result [[0, 0, 99999], [1, 25, 120, 7], [2, 24, 0, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 16, 160, 3]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 13, 200, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 29, 190, 3]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 29, 90, 3]]
result [[0, 0, 99999],

In [20]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 4] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 34, 0, 7], [2, 2, 160, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 15, 130, 4]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 24, 160, 4]]
result [[0, 0, 99999], [1, 16, 90, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 9, 160, 7], [2, 27, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 24, 120, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 15, 100, 4]]
result [[0, 0, 99999], [1, 19, 70, 7], [2, 23, 0, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 18, 140, 4]]
result [[0, 0, 99999], [1, 39, 160, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 21, 80, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 19, 160, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 26, 360, 4]]
result [[0, 0, 99999], [1, 9, 110, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 33, 120, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 12, 180, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 18, 120, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 19, 140, 4]]
result [[0, 0, 999

result [[0, 0, 99999], [1, 34, 0, 7], [2, 31, 220, 4]]
result [[0, 0, 99999], [1, 31, 120, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 2, 280, 4]]
result [[0, 0, 99999], [1, 32, 140, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 17, 100, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 38, 240, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 35, 100, 4]]
result [[0, 0, 99999], [1, 8, 90, 7], [2, 3, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 8, 140, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 34, 280, 4]]
result [[0, 0, 99999], [1, 10, 120, 7], [2, 31, 0, 4]]
result [[0, 0, 99999], [1, 25, 220, 7], [2, 16, 0, 4]]
result [[0, 0, 99999], [1, 1, 100, 7], [2, 14, 0, 4]]
result [[0, 0, 99999], [1, 5, 150, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 17, 60, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 26, 120, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 26, 120, 4]]
result [[0, 0, 99999], [1, 10, 140, 7], [2, 39, 0, 4]]
result [[0, 0, 999

result [[0, 0, 99999], [1, 32, 0, 7], [2, 10, 120, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 29, 80, 4]]
result [[0, 0, 99999], [1, 39, 100, 7], [2, 27, 0, 4]]
result [[0, 0, 99999], [1, 17, 80, 7], [2, 18, 0, 4]]
result [[0, 0, 99999], [1, 28, 60, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 15, 60, 4]]
result [[0, 0, 99999], [1, 9, 110, 7], [2, 23, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 29, 120, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 4, 240, 4]]
result [[0, 0, 99999], [1, 28, 120, 7], [2, 3, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 14, 200, 4]]
result [[0, 0, 99999], [1, 29, 120, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 15, 60, 4]]
result [[0, 0, 99999], [1, 1, 0, 7], [2, 5, 80, 4]]
result [[0, 0, 99999], [1, 28, 100, 7], [2, 8, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 17, 120, 4]]
result [[0, 0, 99999], [1, 26, 120, 7], [2, 14, 0, 4]]
result [[0, 0, 99999], [1, 5, 140, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 21, 80, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 9, 80, 7], [2, 27, 0, 4]]
result [[0, 0, 99999], [1, 12, 180, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 11, 170, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 13, 40, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 39, 360, 4]]
result [[0, 0, 99999], [1, 21, 60, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 1, 140, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 32, 300, 4]]
result [[0, 0, 99999], [1, 28, 60, 7], [2, 6, 0, 4]]
result [[0, 0, 99999], [1, 10, 80, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 11, 100, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 14, 180, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 34, 100, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 35, 140, 4]]
result [[0, 0, 99999], [1, 26, 220, 7], [2, 23, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 37, 80, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 19, 280, 4]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 11, 40, 7], [2, 1, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 38, 260, 4]]
result [[0, 0, 99999], [1, 27, 120, 7], [2, 6, 0, 4]]
result [[0, 0, 99999], [1, 35, 80, 7], [2, 26, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 35, 160, 4]]
result [[0, 0, 99999], [1, 33, 220, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 38, 120, 4]]
result [[0, 0, 99999], [1, 27, 120, 7], [2, 16, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 25, 140, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 12, 90, 4]]
result [[0, 0, 99999], [1, 25, 120, 7], [2, 3, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 38, 200, 4]]
result [[0, 0, 99999], [1, 32, 120, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 2, 240, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 6, 300, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 10, 80, 4]]
result [[0, 0, 99999], [1, 23, 180, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 18, 40, 4]]
result [[0, 0, 99999

...

result [[0, 0, 99999], [1, 3, 0, 7], [2, 5, 120, 4]]
result [[0, 0, 99999], [1, 0, 80, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 24, 130, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 25, 300, 4]]
result [[0, 0, 99999], [1, 19, 60, 7], [2, 32, 0, 4]]
result [[0, 0, 99999], [1, 23, 100, 7], [2, 26, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 31, 80, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 15, 140, 4]]
result [[0, 0, 99999], [1, 1, 120, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 37, 260, 7], [2, 16, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 29, 160, 4]]
result [[0, 0, 99999], [1, 14, 80, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 13, 100, 4]]
result [[0, 0, 99999], [1, 19, 190, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 7, 140, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 26, 200, 4]]
result [[0, 0, 99999], [1, 13, 80, 7], [2, 16, 0, 4]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 32, 0, 7], [2, 32, 280, 4]]
result [[0, 0, 99999], [1, 19, 140, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 18, 80, 7], [2, 23, 0, 4]]
result [[0, 0, 99999], [1, 5, 80, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 35, 120, 7], [2, 32, 0, 4]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 24, 320, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 9, 160, 4]]
result [[0, 0, 99999], [1, 33, 120, 7], [2, 14, 0, 4]]
result [[0, 0, 99999], [1, 28, 180, 7], [2, 18, 0, 4]]
result [[0, 0, 99999], [1, 1, 0, 7], [2, 16, 420, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 20, 170, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 24, 180, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 10, 60, 4]]
result [[0, 0, 99999], [1, 34, 160, 7], [2, 16, 0, 4]]
result [[0, 0, 99999], [1, 6, 160, 7], [2, 21, 0, 4]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 21, 80, 4]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 14, 0, 4]]
result [[0, 0, 9999

result [[0, 0, 99999], [1, 39, 140, 7], [2, 16, 0, 4]]
result [[0, 0, 99999], [1, 13, 100, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 28, 40, 7], [2, 1, 0, 4]]
result [[0, 0, 99999], [1, 10, 200, 7], [2, 16, 0, 4]]
result [[0, 0, 99999], [1, 11, 140, 7], [2, 27, 0, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 16, 130, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 35, 70, 4]]
result [[0, 0, 99999], [1, 33, 100, 7], [2, 29, 0, 4]]
result [[0, 0, 99999], [1, 35, 130, 7], [2, 26, 0, 4]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 33, 140, 4]]
result [[0, 0, 99999], [1, 0, 120, 7], [2, 8, 0, 4]]
result [[0, 0, 99999], [1, 25, 100, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 21, 60, 7], [2, 8, 0, 4]]
result [[0, 0, 99999], [1, 19, 100, 7], [2, 18, 0, 4]]
result [[0, 0, 99999], [1, 9, 120, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 9, 120, 7], [2, 18, 0, 4]]
result [[0, 0, 99999], [1, 37, 0, 7], [2, 13, 90, 4]]
result [[0, 0, 99999], [1, 20, 120, 7], [2, 11, 0, 4]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 21, 100, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 32, 160, 7], [2, 14, 0, 4]]
result [[0, 0, 99999], [1, 18, 60, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 38, 20, 7], [2, 8, 0, 4]]
result [[0, 0, 99999], [1, 28, 140, 7], [2, 6, 0, 4]]
result [[0, 0, 99999], [1, 16, 40, 7], [2, 1, 0, 4]]
result [[0, 0, 99999], [1, 34, 0, 7], [2, 34, 40, 4]]
result [[0, 0, 99999], [1, 28, 120, 7], [2, 23, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 31, 80, 4]]
result [[0, 0, 99999], [1, 23, 100, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 6, 120, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 39, 240, 4]]
result [[0, 0, 99999], [1, 28, 100, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 37, 220, 7], [2, 11, 0, 4]]
result [[0, 0, 99999], [1, 23, 100, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 28, 80, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [1, 32, 70, 7], [2, 23, 0, 4]]
result [[0, 0, 99999], [1, 18, 160, 7], [2, 3, 0, 4]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 34, 0, 7], [2, 24, 80, 4]]
result [[0, 0, 99999], [1, 20, 60, 7], [2, 26, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 16, 200, 4]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 17, 120, 4]]
result [[0, 0, 99999], [1, 25, 100, 7], [2, 26, 0, 4]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 18, 0, 4]]
result [[0, 0, 99999], [1, 26, 60, 7], [2, 13, 0, 4]]
result [[0, 0, 99999], [1, 12, 70, 7], [2, 24, 0, 4]]
result [[0, 0, 99999], [1, 18, 20, 7], [2, 19, 0, 4]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 24, 120, 4]]
result [[0, 0, 99999], [1, 37, 100, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 32, 100, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 12, 160, 4]]
result [[0, 0, 99999], [1, 9, 50, 7], [2, 9, 0, 4]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 17, 300, 4]]
result [[0, 0, 99999], [1, 29, 80, 7], [2, 6, 0, 4]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 28, 100, 4]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 15, 140, 4]]
result [[0, 0, 99999], [

In [21]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 5] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 9, 0, 7], [2, 9, 80, 5]]
result [[0, 0, 99999], [1, 32, 80, 7], [2, 8, 0, 5]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 23, 200, 5]]
result [[0, 0, 99999], [1, 18, 140, 7], [2, 19, 0, 5]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 23, 120, 5]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 24, 100, 5]]
result [[0, 0, 99999], [1, 31, 100, 7], [2, 26, 0, 5]]
result [[0, 0, 99999], [1, 0, 60, 7], [2, 9, 0, 5]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 19, 100, 5]]
result [[0, 0, 99999], [1, 4, 60, 7], [2, 19, 0, 5]]
result [[0, 0, 99999], [1, 21, 140, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 2, 120, 5]]
result [[0, 0, 99999], [1, 28, 20, 7], [2, 14, 0, 5]]
result [[0, 0, 99999], [1, 16, 80, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 2, 100, 7], [2, 8, 0, 5]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 28, 120, 5]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 37, 120, 5]]
result [[0, 0, 99999], [1, 10, 240, 7], [2, 39, 0, 5]]
result [[0, 0, 99999], [1, 

result [[0, 0, 99999], [1, 18, 0, 7], [2, 33, 60, 5]]
result [[0, 0, 99999], [1, 9, 220, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 25, 40, 7], [2, 9, 0, 5]]
result [[0, 0, 99999], [1, 10, 140, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 39, 60, 7], [2, 6, 0, 5]]
result [[0, 0, 99999], [1, 28, 120, 7], [2, 27, 0, 5]]
result [[0, 0, 99999], [1, 17, 60, 7], [2, 14, 0, 5]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 27, 180, 5]]
result [[0, 0, 99999], [1, 3, 200, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 24, 160, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 16, 80, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 38, 80, 5]]
result [[0, 0, 99999], [1, 8, 40, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 10, 60, 5]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 38, 20, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 1, 120, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 35, 40, 5]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 26, 100, 5]]
result [[0, 0, 99999], [1, 

result [[0, 0, 99999], [1, 28, 160, 7], [2, 11, 0, 5]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 15, 200, 5]]
result [[0, 0, 99999], [1, 3, 80, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 25, 100, 5]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 31, 120, 5]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 13, 140, 5]]
result [[0, 0, 99999], [1, 4, 80, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 3, 100, 7], [2, 34, 0, 5]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 12, 120, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 33, 80, 5]]
result [[0, 0, 99999], [1, 19, 40, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 13, 40, 5]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 10, 120, 5]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 3, 80, 5]]
result [[0, 0, 99999], [1, 23, 180, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 21, 60, 7], [2, 8, 0, 5]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 39, 20, 5]]
result [[0, 0, 99999], [1, 12, 200, 7], [2, 27, 0, 5]]
result [[0, 0, 99999], [

result [[0, 0, 99999], [1, 16, 0, 7], [2, 29, 180, 5]]
result [[0, 0, 99999], [1, 34, 160, 7], [2, 23, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 17, 120, 5]]
result [[0, 0, 99999], [1, 25, 70, 7], [2, 37, 0, 5]]
result [[0, 0, 99999], [1, 27, 120, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 29, 200, 5]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 21, 80, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 22, 160, 5]]
result [[0, 0, 99999], [1, 22, 60, 7], [2, 32, 0, 5]]
result [[0, 0, 99999], [1, 31, 180, 7], [2, 9, 0, 5]]
result [[0, 0, 99999], [1, 14, 60, 7], [2, 11, 0, 5]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 13, 160, 5]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 17, 120, 5]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 33, 120, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 10, 340, 5]]
result [[0, 0, 99999], [1, 16, 100, 7], [2, 14, 0, 5]]
result [[0, 0, 99999], [1, 38, 160, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], [1, 39, 80, 7], [2, 9, 0, 5]]
result [[0, 0, 9999

result [[0, 0, 99999], [1, 37, 80, 7], [2, 27, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 25, 120, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 3, 160, 5]]
result [[0, 0, 99999], [1, 15, 40, 7], [2, 3, 0, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 10, 160, 5]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 3, 80, 5]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 29, 80, 5]]
result [[0, 0, 99999], [1, 5, 120, 7], [2, 1, 0, 5]]
result [[0, 0, 99999], [1, 15, 100, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 17, 140, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 7, 140, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 3, 60, 5]]
result [[0, 0, 99999], [1, 1, 60, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 11, 120, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 19, 320, 5]]
result [[0, 0, 99999], [1, 5, 100, 7], [2, 23, 0, 5]]
result [[0, 0, 99999], [1, 10, 100, 7], [2, 11, 0, 5]]
result [[0, 0, 99999], [1, 12, 60, 7], [2, 8, 0, 5]]
result [[0, 0, 99999], [1, 2

...

result [[0, 0, 99999], [1, 3, 0, 7], [2, 1, 40, 5]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 25, 180, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 15, 140, 5]]
result [[0, 0, 99999], [1, 3, 120, 7], [2, 19, 0, 5]]
result [[0, 0, 99999], [1, 14, 180, 7], [2, 31, 0, 5]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 27, 80, 5]]
result [[0, 0, 99999], [1, 31, 80, 7], [2, 11, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 31, 140, 5]]
result [[0, 0, 99999], [1, 19, 20, 7], [2, 3, 0, 5]]
result [[0, 0, 99999], [1, 2, 100, 7], [2, 23, 0, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 10, 80, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 10, 80, 5]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 17, 180, 5]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 15, 60, 5]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 33, 140, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 21, 60, 5]]
result [[0, 0, 99999], [1, 10, 100, 7], [2, 14, 0, 5]]
result [[0, 0, 99999], [1, 10, 80, 7], [2, 39, 0, 5]]
result [[0, 0, 99999], [1,

result [[0, 0, 99999], [1, 11, 0, 7], [2, 27, 160, 5]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 0, 260, 5]]
result [[0, 0, 99999], [1, 25, 100, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 8, 160, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 2, 80, 7], [2, 34, 0, 5]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 34, 140, 5]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 27, 60, 5]]
result [[0, 0, 99999], [1, 10, 40, 7], [2, 3, 0, 5]]
result [[0, 0, 99999], [1, 20, 60, 7], [2, 29, 0, 5]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 17, 200, 5]]
result [[0, 0, 99999], [1, 18, 40, 7], [2, 31, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 32, 280, 5]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 19, 100, 5]]
result [[0, 0, 99999], [1, 35, 140, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 39, 40, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 25, 160, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 34, 160, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 18, 100, 5]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 33, 200, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 25, 100, 7], [2, 27, 0, 5]]
result [[0, 0, 99999], [1, 29, 100, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 2, 120, 7], [2, 9, 0, 5]]
result [[0, 0, 99999], [1, 11, 80, 7], [2, 19, 0, 5]]
result [[0, 0, 99999], [1, 15, 60, 7], [2, 9, 0, 5]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 21, 160, 5]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 19, 80, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 24, 160, 5]]
result [[0, 0, 99999], [1, 31, 300, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 16, 40, 5]]
result [[0, 0, 99999], [1, 4, 160, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 22, 100, 5]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 29, 80, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 16, 200, 5]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 7, 60, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 8, 140, 5]]
result [[0, 0, 99999], [1, 15, 100, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 20, 120, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 19, 60, 5]]
result [[0, 0, 99999], [1, 26, 40, 7], [2, 13, 0, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 6, 120, 5]]
result [[0, 0, 99999], [1, 19, 100, 7], [2, 8, 0, 5]]
result [[0, 0, 99999], [1, 25, 40, 7], [2, 3, 0, 5]]
result [[0, 0, 99999], [1, 10, 60, 7], [2, 3, 0, 5]]
result [[0, 0, 99999], [1, 23, 100, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 18, 60, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 19, 60, 5]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 2, 80, 5]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 23, 80, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 11, 100, 5]]
result [[0, 0, 99999], [1, 36, 120, 7], [2, 13, 0, 5]]
result [[0, 0, 99999], [1, 3, 80, 7], [2, 23, 0, 5]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 10, 220, 5]]
result [[0, 0, 99999], [1, 19, 200, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 35, 100, 7], [2, 9, 0, 5]]
result [[0, 0, 99999], [1,

result [[0, 0, 99999], [1, 21, 0, 7], [2, 17, 60, 5]]
result [[0, 0, 99999], [1, 25, 160, 7], [2, 8, 0, 5]]
result [[0, 0, 99999], [1, 15, 80, 7], [2, 26, 0, 5]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 0, 120, 5]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 23, 140, 5]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 38, 80, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 6, 80, 5]]
result [[0, 0, 99999], [1, 5, 20, 7], [2, 16, 0, 5]]
result [[0, 0, 99999], [1, 8, 120, 7], [2, 6, 0, 5]]
result [[0, 0, 99999], [1, 27, 100, 7], [2, 24, 0, 5]]
result [[0, 0, 99999], [1, 18, 80, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1, 2, 160, 7], [2, 18, 0, 5]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 10, 140, 5]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 19, 40, 5]]
result [[0, 0, 99999], [1, 4, 60, 7], [2, 34, 0, 5]]
result [[0, 0, 99999], [1, 34, 120, 7], [2, 32, 0, 5]]
result [[0, 0, 99999], [1, 23, 160, 7], [2, 21, 0, 5]]
result [[0, 0, 99999], [1,

In [22]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 6] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 3, 40, 7], [2, 14, 0, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 0, 140, 6]]
result [[0, 0, 99999], [1, 38, 80, 7], [2, 14, 0, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 1, 160, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 17, 40, 6]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 15, 160, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 26, 140, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 19, 60, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 28, 60, 6]]
result [[0, 0, 99999], [1, 12, 200, 7], [2, 11, 0, 6]]
result [[0, 0, 99999], [1, 17, 20, 7], [2, 6, 0, 6]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 31, 120, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 12, 220, 6]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 24, 300, 6]]
result [[0, 0, 99999], [1, 21, 40, 7], [2, 18, 0, 6]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 31, 100, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 16, 140, 6]]
result [[0, 0, 99999], [1, 24, 120, 7], [2, 32, 0, 6]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 19, 0, 7], [2, 4, 40, 6]]
result [[0, 0, 99999], [1, 39, 200, 7], [2, 29, 0, 6]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 13, 400, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 19, 180, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 12, 160, 6]]
result [[0, 0, 99999], [1, 9, 60, 7], [2, 11, 0, 6]]
result [[0, 0, 99999], [1, 26, 40, 7], [2, 6, 0, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 27, 160, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 11, 60, 6]]
result [[0, 0, 99999], [1, 5, 140, 7], [2, 8, 0, 6]]
result [[0, 0, 99999], [1, 33, 160, 7], [2, 13, 0, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 1, 260, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 19, 140, 6]]
result [[0, 0, 99999], [1, 17, 100, 7], [2, 6, 0, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 21, 80, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 8, 60, 6]]
result [[0, 0, 99999], [1, 0, 100, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 5, 240, 6]]
result [[0, 0, 99999], [1, 10

result [[0, 0, 99999], [1, 25, 80, 7], [2, 9, 0, 6]]
result [[0, 0, 99999], [1, 20, 120, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 37, 40, 7], [2, 3, 0, 6]]
result [[0, 0, 99999], [1, 39, 140, 7], [2, 11, 0, 6]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 26, 60, 6]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 18, 220, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 27, 170, 6]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 34, 140, 6]]
result [[0, 0, 99999], [1, 28, 180, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 12, 60, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 15, 40, 7], [2, 13, 0, 6]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 10, 220, 6]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 26, 40, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 4, 140, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 25, 80, 6]]
result [[0, 0, 99999], [1, 20, 160, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 35, 100, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 2, 160, 6]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 16, 0, 7], [2, 24, 40, 6]]
result [[0, 0, 99999], [1, 3, 160, 7], [2, 29, 0, 6]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 11, 60, 6]]
result [[0, 0, 99999], [1, 15, 60, 7], [2, 6, 0, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 28, 120, 6]]
result [[0, 0, 99999], [1, 13, 40, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 19, 40, 7], [2, 24, 0, 6]]
result [[0, 0, 99999], [1, 39, 0, 7], [2, 16, 140, 6]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 28, 80, 6]]
result [[0, 0, 99999], [1, 21, 100, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 23, 120, 6]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 18, 60, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 2, 260, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 34, 120, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 18, 200, 6]]
result [[0, 0, 99999], [1, 12, 160, 7], [2, 11, 0, 6]]
result [[0, 0, 99999], [1, 15, 180, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 12, 200, 6]]
result [[0, 0, 99999]

result [[0, 0, 99999], [1, 14, 0, 7], [2, 11, 140, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 38, 300, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 3, 200, 6]]
result [[0, 0, 99999], [1, 3, 220, 7], [2, 39, 0, 6]]
result [[0, 0, 99999], [1, 33, 120, 7], [2, 31, 0, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 17, 140, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 31, 60, 6]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 33, 80, 6]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 28, 80, 6]]
result [[0, 0, 99999], [1, 35, 180, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 2, 80, 7], [2, 9, 0, 6]]
result [[0, 0, 99999], [1, 33, 60, 7], [2, 6, 0, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 20, 40, 6]]
result [[0, 0, 99999], [1, 3, 100, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 14, 80, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 39, 140, 6]]
result [[0, 0, 99999], [1, 16, 100, 7], [2, 14, 0, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 5, 120, 6]]
result [[0, 0, 99999], [1,

...

result [[0, 0, 99999], [1, 14, 0, 7], [2, 19, 140, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 27, 160, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 10, 120, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 32, 160, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 26, 60, 6]]
result [[0, 0, 99999], [1, 4, 60, 7], [2, 24, 0, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 36, 220, 6]]
result [[0, 0, 99999], [1, 17, 160, 7], [2, 24, 0, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 23, 160, 6]]
result [[0, 0, 99999], [1, 0, 120, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 39, 140, 7], [2, 18, 0, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 37, 120, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 38, 40, 6]]
result [[0, 0, 99999], [1, 39, 80, 7], [2, 14, 0, 6]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 16, 100, 6]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 10, 140, 6]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 10, 100, 6]]
result [[0, 0, 99999], [1, 7, 100, 7], [2, 9, 0, 6]]
result [[0, 0, 999

result [[0, 0, 99999], [1, 11, 0, 7], [2, 10, 160, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 27, 300, 6]]
result [[0, 0, 99999], [1, 20, 100, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 38, 80, 7], [2, 9, 0, 6]]
result [[0, 0, 99999], [1, 22, 220, 7], [2, 13, 0, 6]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 6, 160, 6]]
result [[0, 0, 99999], [1, 8, 40, 7], [2, 8, 0, 6]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 25, 160, 6]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 6, 140, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 20, 140, 6]]
result [[0, 0, 99999], [1, 25, 100, 7], [2, 13, 0, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 16, 200, 6]]
result [[0, 0, 99999], [1, 5, 50, 7], [2, 1, 0, 6]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 38, 80, 6]]
result [[0, 0, 99999], [1, 20, 200, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 24, 40, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 15, 120, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 6, 240, 6]]
result [[0, 0, 99999], 

result [[0, 0, 99999], [1, 32, 0, 7], [2, 4, 120, 6]]
result [[0, 0, 99999], [1, 39, 20, 7], [2, 6, 0, 6]]
result [[0, 0, 99999], [1, 21, 40, 7], [2, 3, 0, 6]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 20, 100, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 19, 140, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 32, 100, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 6, 60, 6]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 10, 260, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 31, 220, 6]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 14, 120, 6]]
result [[0, 0, 99999], [1, 18, 180, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 17, 100, 6]]
result [[0, 0, 99999], [1, 39, 80, 7], [2, 24, 0, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 25, 40, 6]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 1, 100, 6]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 39, 80, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 25, 180, 6]]
result [[0, 0, 99999], [1, 19, 140, 7], [2, 3, 0, 6]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 5, 80, 7], [2, 16, 0, 6]]
result [[0, 0, 99999], [1, 21, 100, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 12, 60, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 15, 120, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 10, 200, 6]]
result [[0, 0, 99999], [1, 12, 220, 7], [2, 18, 0, 6]]
result [[0, 0, 99999], [1, 9, 20, 7], [2, 21, 0, 6]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 0, 220, 6]]
result [[0, 0, 99999], [1, 5, 120, 7], [2, 13, 0, 6]]
result [[0, 0, 99999], [1, 25, 60, 7], [2, 9, 0, 6]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 0, 240, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 15, 120, 6]]
result [[0, 0, 99999], [1, 0, 40, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 10, 80, 6]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 28, 140, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 31, 80, 6]]
result [[0, 0, 99999], [1, 6, 20, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 11, 100, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1,

result [[0, 0, 99999], [1, 34, 0, 7], [2, 27, 60, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 14, 160, 6]]
result [[0, 0, 99999], [1, 8, 40, 7], [2, 27, 0, 6]]
result [[0, 0, 99999], [1, 20, 120, 7], [2, 8, 0, 6]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 29, 40, 6]]
result [[0, 0, 99999], [1, 35, 60, 7], [2, 8, 0, 6]]
result [[0, 0, 99999], [1, 26, 80, 7], [2, 18, 0, 6]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 5, 60, 6]]
result [[0, 0, 99999], [1, 2, 100, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 9, 120, 7], [2, 3, 0, 6]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 13, 160, 6]]
result [[0, 0, 99999], [1, 25, 80, 7], [2, 19, 0, 6]]
result [[0, 0, 99999], [1, 25, 80, 7], [2, 18, 0, 6]]
result [[0, 0, 99999], [1, 0, 160, 7], [2, 26, 0, 6]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 33, 140, 6]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 1, 200, 6]]
result [[0, 0, 99999], [1, 1, 80, 7], [2, 9, 0, 6]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 13, 160, 6]]
result [[0, 0, 99999], [1, 11,

In [23]:
def init():
    global test_player1
    global test_player2
    global playerList
    global housePurchase
    global debugSw
    test_player1 = [1, 0, 500, 7] #buy all
    test_player2 = [2, 0, 500, 8] #only buy cheap
    playerList = [[0, 0 ,99999], test_player1, test_player2]
    housePurchase = [0] * 40
    debugSw = False
    
loseTime = [0] * 10
for i in range(10000):
    init()
    a = game()
    loseTime[a] += 1
    
print(loseTime)

result [[0, 0, 99999], [1, 24, 0, 7], [2, 8, 100, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 9, 420, 8]]
result [[0, 0, 99999], [1, 14, 180, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 9, 60, 8]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 1, 160, 8]]
result [[0, 0, 99999], [1, 10, 140, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 3, 320, 8]]
result [[0, 0, 99999], [1, 11, 40, 7], [2, 26, 0, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 10, 140, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 25, 100, 8]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 23, 200, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 16, 80, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 17, 160, 8]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 28, 280, 8]]
result [[0, 0, 99999], [1, 33, 80, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 1, 140, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 14, 100, 8]]
result [[0, 0, 99999], [1, 13, 120, 7], [2, 18, 0, 8]]
result [[0, 0, 99999],

result [[0, 0, 99999], [1, 16, 0, 7], [2, 31, 100, 8]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 25, 120, 8]]
result [[0, 0, 99999], [1, 19, 100, 7], [2, 24, 0, 8]]
result [[0, 0, 99999], [1, 15, 160, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 23, 240, 8]]
result [[0, 0, 99999], [1, 10, 80, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 20, 40, 8]]
result [[0, 0, 99999], [1, 34, 220, 7], [2, 24, 0, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 14, 100, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 21, 40, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 24, 160, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 32, 220, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 20, 60, 8]]
result [[0, 0, 99999], [1, 22, 200, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 9, 120, 7], [2, 14, 0, 8]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 21, 80, 8]]
result [[0, 0, 99999], [1, 24, 40, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 14, 120, 8]]
result [[0, 0, 999

result [[0, 0, 99999], [1, 23, 0, 7], [2, 31, 60, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 19, 100, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 28, 80, 8]]
result [[0, 0, 99999], [1, 12, 120, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 27, 100, 8]]
result [[0, 0, 99999], [1, 1, 100, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 1, 80, 8]]
result [[0, 0, 99999], [1, 10, 180, 7], [2, 26, 0, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 20, 120, 8]]
result [[0, 0, 99999], [1, 38, 100, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 24, 60, 7], [2, 9, 0, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 5, 80, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 35, 120, 8]]
result [[0, 0, 99999], [1, 38, 80, 7], [2, 9, 0, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 25, 80, 8]]
result [[0, 0, 99999], [1, 9, 80, 7], [2, 9, 0, 8]]
result [[0, 0, 99999], [1, 37, 120, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 24, 120, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1

result [[0, 0, 99999], [1, 14, 100, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 25, 120, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 38, 200, 8]]
result [[0, 0, 99999], [1, 38, 220, 7], [2, 8, 0, 8]]
result [[0, 0, 99999], [1, 9, 160, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 23, 100, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 31, 120, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 13, 120, 7], [2, 21, 0, 8]]
result [[0, 0, 99999], [1, 17, 180, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 38, 20, 8]]
result [[0, 0, 99999], [1, 37, 60, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 15, 100, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 10, 80, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 36, 160, 8]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 14, 140, 8]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 10, 200, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 10, 140, 8]]
result [[0, 0, 99999], [1, 25, 60, 7], [2, 14, 0, 8]]
result [[0, 0, 9999

result [[0, 0, 99999], [1, 20, 180, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 15, 220, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 17, 140, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 6, 200, 8]]
result [[0, 0, 99999], [1, 22, 120, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 10, 140, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 15, 160, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 27, 60, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 5, 160, 8]]
result [[0, 0, 99999], [1, 1, 100, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 0, 80, 8]]
result [[0, 0, 99999], [1, 6, 80, 7], [2, 9, 0, 8]]
result [[0, 0, 99999], [1, 29, 60, 7], [2, 6, 0, 8]]
result [[0, 0, 99999], [1, 24, 140, 7], [2, 31, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 38, 120, 8]]
result [[0, 0, 99999], [1, 6, 0, 7], [2, 21, 80, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 5, 140, 8]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 2, 60, 8]]
result [[0, 0, 99999], [1, 1

...

result [[0, 0, 99999], [1, 9, 0, 7], [2, 21, 80, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 24, 40, 8]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 31, 80, 8]]
result [[0, 0, 99999], [1, 27, 140, 7], [2, 23, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 12, 40, 8]]
result [[0, 0, 99999], [1, 33, 100, 7], [2, 21, 0, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 8, 140, 8]]
result [[0, 0, 99999], [1, 8, 140, 7], [2, 29, 0, 8]]
result [[0, 0, 99999], [1, 3, 0, 7], [2, 32, 100, 8]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 10, 160, 8]]
result [[0, 0, 99999], [1, 38, 160, 7], [2, 21, 0, 8]]
result [[0, 0, 99999], [1, 27, 80, 7], [2, 26, 0, 8]]
result [[0, 0, 99999], [1, 5, 120, 7], [2, 31, 0, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 10, 120, 8]]
result [[0, 0, 99999], [1, 0, 60, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 1, 200, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 12, 60, 8]]
result [[0, 0, 99999], [1, 29, 0, 7], [2, 10, 160, 8]]
result [[0, 0, 99999], [1,

result [[0, 0, 99999], [1, 34, 60, 7], [2, 23, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 34, 160, 8]]
result [[0, 0, 99999], [1, 0, 40, 7], [2, 29, 0, 8]]
result [[0, 0, 99999], [1, 8, 0, 7], [2, 34, 40, 8]]
result [[0, 0, 99999], [1, 15, 40, 7], [2, 8, 0, 8]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 18, 200, 8]]
result [[0, 0, 99999], [1, 26, 0, 7], [2, 8, 80, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 37, 260, 8]]
result [[0, 0, 99999], [1, 18, 0, 7], [2, 32, 110, 8]]
result [[0, 0, 99999], [1, 33, 100, 7], [2, 34, 0, 8]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 17, 80, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 13, 100, 8]]
result [[0, 0, 99999], [1, 17, 20, 7], [2, 3, 0, 8]]
result [[0, 0, 99999], [1, 0, 80, 7], [2, 14, 0, 8]]
result [[0, 0, 99999], [1, 32, 100, 7], [2, 19, 0, 8]]
result [[0, 0, 99999], [1, 0, 160, 7], [2, 16, 0, 8]]
result [[0, 0, 99999], [1, 23, 160, 7], [2, 9, 0, 8]]
result [[0, 0, 99999], [1, 0, 100, 7], [2, 21, 0, 8]]
result [[0, 0, 99999], [1, 1

result [[0, 0, 99999], [1, 29, 0, 7], [2, 26, 40, 8]]
result [[0, 0, 99999], [1, 10, 220, 7], [2, 23, 0, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 11, 120, 8]]
result [[0, 0, 99999], [1, 0, 220, 7], [2, 3, 0, 8]]
result [[0, 0, 99999], [1, 28, 140, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 5, 100, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 0, 80, 8]]
result [[0, 0, 99999], [1, 29, 140, 7], [2, 24, 0, 8]]
result [[0, 0, 99999], [1, 32, 0, 7], [2, 25, 80, 8]]
result [[0, 0, 99999], [1, 18, 100, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 0, 220, 8]]
result [[0, 0, 99999], [1, 31, 0, 7], [2, 34, 120, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 4, 140, 8]]
result [[0, 0, 99999], [1, 21, 0, 7], [2, 26, 140, 8]]
result [[0, 0, 99999], [1, 10, 160, 7], [2, 23, 0, 8]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 39, 120, 8]]
result [[0, 0, 99999], [1, 22, 160, 7], [2, 18, 0, 8]]
result [[0, 0, 99999], [1, 34, 180, 7], [2, 19, 0, 8]]
result [[0, 0, 99999

result [[0, 0, 99999], [1, 11, 0, 7], [2, 15, 60, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 33, 120, 8]]
result [[0, 0, 99999], [1, 33, 80, 7], [2, 13, 0, 8]]
result [[0, 0, 99999], [1, 26, 120, 7], [2, 14, 0, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 9, 120, 8]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 32, 60, 8]]
result [[0, 0, 99999], [1, 24, 100, 7], [2, 23, 0, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 0, 80, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 15, 140, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 15, 100, 8]]
result [[0, 0, 99999], [1, 37, 20, 7], [2, 9, 0, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 11, 60, 8]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 29, 100, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 32, 160, 8]]
result [[0, 0, 99999], [1, 24, 0, 7], [2, 25, 100, 8]]
result [[0, 0, 99999], [1, 11, 0, 7], [2, 4, 200, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 27, 100, 8]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 29, 120, 8]]
result [[0, 0, 99999

result [[0, 0, 99999], [1, 16, 0, 7], [2, 15, 180, 8]]
result [[0, 0, 99999], [1, 27, 0, 7], [2, 10, 180, 8]]
result [[0, 0, 99999], [1, 14, 0, 7], [2, 15, 80, 8]]
result [[0, 0, 99999], [1, 23, 120, 7], [2, 24, 0, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 0, 80, 8]]
result [[0, 0, 99999], [1, 33, 100, 7], [2, 3, 0, 8]]
result [[0, 0, 99999], [1, 16, 0, 7], [2, 10, 140, 8]]
result [[0, 0, 99999], [1, 9, 60, 7], [2, 21, 0, 8]]
result [[0, 0, 99999], [1, 13, 0, 7], [2, 10, 40, 8]]
result [[0, 0, 99999], [1, 20, 240, 7], [2, 21, 0, 8]]
result [[0, 0, 99999], [1, 35, 220, 7], [2, 11, 0, 8]]
result [[0, 0, 99999], [1, 31, 80, 7], [2, 26, 0, 8]]
result [[0, 0, 99999], [1, 18, 100, 7], [2, 32, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 39, 160, 8]]
result [[0, 0, 99999], [1, 19, 0, 7], [2, 2, 180, 8]]
result [[0, 0, 99999], [1, 23, 0, 7], [2, 24, 120, 8]]
result [[0, 0, 99999], [1, 28, 100, 7], [2, 23, 0, 8]]
result [[0, 0, 99999], [1, 9, 0, 7], [2, 11, 80, 8]]
result [[0, 0, 99999],